In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

from pyathena import connect
import pandas as pd
import json

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', None)

conn = connect(s3_staging_dir='s3://jm-dsprod-athena/data-scientist-workgroup', region_name='ap-south-1',)

%load_ext athena

#pd.read_sql("show tables in delta_lake_db '*customer*';", conn)
#df  = pd.read_sql("SELECT * FROM delta_lake_db.customer_success_jupiter_tickets limit 1;", conn)

In [ ]:
%%athena
--dwh query - June 21 users; kyc status till June 22 End; 365 days and June 22 month eod balance avg
with 
base as (
    select distinct
        onboarding_account.user_id,
        onboarding_account.savings_account_created_at,
        onboarding_account.account_type,
        aux_updated_at,
        datediff(minute, savings_account_created_at, aux_updated_at) as conversion_time
    from dwh_onboarding.stg_onboarding_public_customer_account_infoset onboarding_account
    where account_provisioning_type = 'jupiter.accounts.provisioning.liability-primary'
),

ob_computed as (
    select
        user_id,
        date(savings_account_created_at) savings_account_created_date,
        date(aux_updated_at) kyc_update_date,
        case
            when account_type = 'jupiter.accounts.full' and conversion_time < 30 then 'ETB'
            when account_type = 'jupiter.accounts.full' and conversion_time >= 30 then 'VKYC'
            when account_type = 'jupiter.accounts.half' then 'HKYC'
            else 'None'
        end as kyc_mode_temp
    from base
),

ob_final as 
(
 select user_id
    , savings_account_created_date 
    , kyc_update_date
    , kyc_mode_temp
    , case when kyc_mode_temp = 'VKYC' and kyc_update_date > date('2022-06-30') then 'HKYC'
           else kyc_mode_temp
      end as kyc_mode
 from ob_computed
 where savings_account_created_date between date('2021-06-01') and date('2021-06-30')
),

eod_balance_avg as 
(
select user_id, avg(day_end_balance) as june_22_eod_balance_avg
from
(
select user_id
    , update_date
    , savings_account_created_date
    , case when day_end_balance < 0 then 0 else day_end_balance end as day_end_balance 
from dwh_jupiter_account_balance.fact_jupiter_user_balance_summary
where update_date between date('2022-06-01') and date('2022-06-30')  
 and user_id in (select user_id from ob_final)
)
group by 1 
),

eod_balance_avg_365 as 
(
select user_id, avg(day_end_balance) as eod_balance_avg_365_days
from
(
select user_id
    , update_date
    , savings_account_created_date
    , case when day_end_balance < 0 then 0 else day_end_balance end as day_end_balance 
from dwh_jupiter_account_balance.fact_jupiter_user_balance_summary
where user_id in (select user_id from ob_final)
 and date_diff('day',savings_account_created_date,update_date) <= 365
)
group by 1 
)

select a.user_id, savings_account_created_date, kyc_mode, b.june_22_eod_balance_avg, c.eod_balance_avg_365_days from ob_final a
left join eod_balance_avg b on a.user_id = b.user_id
left join eod_balance_avg_365 c on a.user_id = c.user_id


In [ ]:
%%athena
--dwh query - May 21 users; kyc status till May & June 22 End; 365 days, May 22 month and June 22 month eod balance avg
with 
base as (
    select distinct
        onboarding_account.user_id,
        onboarding_account.savings_account_created_at,
        onboarding_account.account_type,
        aux_updated_at,
        datediff(minute, savings_account_created_at, aux_updated_at) as conversion_time
    from dwh_onboarding.stg_onboarding_public_customer_account_infoset onboarding_account
    where account_provisioning_type = 'jupiter.accounts.provisioning.liability-primary'
),

ob_computed as (
    select
        user_id,
        date(savings_account_created_at) savings_account_created_date,
        date(aux_updated_at) kyc_update_date,
        case
            when account_type = 'jupiter.accounts.full' and conversion_time < 30 then 'ETB'
            when account_type = 'jupiter.accounts.full' and conversion_time >= 30 then 'VKYC'
            when account_type = 'jupiter. accounts.half' then 'HKYC'
            else 'None'
        end as kyc_mode_temp
    from base
),

ob_final as 
(
 select user_id
    , savings_account_created_date 
    , kyc_update_date
    , kyc_mode_temp
    , case when kyc_mode_temp = 'VKYC' and kyc_update_date > date('2022-05-31') then 'HKYC'
           else kyc_mode_temp
      end as kyc_mode_may_22_end
    , case when kyc_mode_temp = 'VKYC' and kyc_update_date > date('2022-06-30') then 'HKYC'
           else kyc_mode_temp
      end as kyc_mode_june_22_end
 from ob_computed
 where savings_account_created_date between date('2021-05-01') and date('2021-05-31')
),

eod_balance_avg as 
(
select user_id, avg(day_end_balance) as may_22_eod_balance_avg
from
(
select user_id
    , update_date
    , savings_account_created_date
    , case when day_end_balance < 0 then 0 else day_end_balance end as day_end_balance 
from dwh_jupiter_account_balance.fact_jupiter_user_balance_summary
where update_date between date('2022-05-01') and date('2022-05-31')  
 and user_id in (select user_id from ob_final)
)
group by 1 
),

eod_balance_avg_2 as 
(
select user_id, avg(day_end_balance) as june_22_eod_balance_avg
from
(
select user_id
    , update_date
    , savings_account_created_date
    , case when day_end_balance < 0 then 0 else day_end_balance end as day_end_balance 
from dwh_jupiter_account_balance.fact_jupiter_user_balance_summary
where update_date between date('2022-06-01') and date('2022-06-30')  
 and user_id in (select user_id from ob_final)
)
group by 1 
),

eod_balance_avg_365 as 
(
select user_id, avg(day_end_balance) as eod_balance_avg_365_days
from
(
select user_id
    , update_date
    , savings_account_created_date
    , case when day_end_balance < 0 then 0 else day_end_balance end as day_end_balance 
from dwh_jupiter_account_balance.fact_jupiter_user_balance_summary
where user_id in (select user_id from ob_final)
 and date_diff('day',savings_account_created_date,update_date) <= 365
)
group by 1 
)

select a.user_id, savings_account_created_date, kyc_mode_may_22_end, kyc_mode_june_22_end
    , b.may_22_eod_balance_avg, d.june_22_eod_balance_avg
    , c.eod_balance_avg_365_days 
from ob_final a
left join eod_balance_avg b on a.user_id = b.user_id
left join eod_balance_avg_2 d on a.user_id = d.user_id
left join eod_balance_avg_365 c on a.user_id = c.user_id


In [ ]:
%%athena
--getting primary account_number (account_id) for an user_id
--you will be able to get info for only user who ever did a txn through primary account
--for the missing ones reach out to Sanjay Gandhi or Sagar Chauhan to get user-id to account-id mapping or vice-versa
    select account_id, user_id from
    
    (select account_id, user_id 
    from dwh_reconciled_transactions.stg_reconciled_transactions_success_transactions
    where user_id in
    
    (
    select distinct onboarding_account.user_id 
    from dwh_onboarding.stg_onboarding_public_customer_account_infoset onboarding_account
    where account_provisioning_type = 'jupiter.accounts.provisioning.liability-primary'
    and date(savings_account_created_at) between date('2021-05-01') and date('2021-06-30')
    )

    and upper(account_id) not like '%XX%'
    group by 1, 2
    order by 2, 1
    ) a
    
    left join (select 
        identifier,
        type, 
        description, 
        ledger_id, 
        balance
    from delta_lake.banking_accounting_accounts
    group by 1, 2, 3, 4, 5
    ) b on a.account_id = b.identifier
    
    where lower(description) like '%savings%'

In [25]:
%%athena
--in-app & off-app txns counts for Apr 22 to July 22 for July 21 users
with
recon_users as
(select *
from transformations_db.jupiter_reconciliation_transaction_master as t1
where updated_at = (select max(updated_at) from transformations_db.jupiter_reconciliation_transaction_master as t2
                   where t1.reconciliation_id = t2.reconciliation_id
and (payments_log_payer_particulars <> 'Jupiter Rewards' OR payments_log_payer_particulars is null)
and (lower(payments_log_payer_particulars) not like '%transfer%pot%' OR payments_log_payer_particulars is null)
and (lower(payments_log_payer_particulars) not like '%withdraw%pot%' OR payments_log_payer_particulars is null)
and (t2.reconciliation_status in ('RECONCILIATION_SUCCESSFUL','RECONCILIATION_CBS_INITIATED')
        OR (account_id like '%XX%'and t2.reconciliation_status in ('RECONCILIATION_JUPITER_SUCCESS'))) 
)
 and customer_id in (select distinct prospective_user_id from transformations_db.jupiter_onboarding_master 
                 where date(user_saving_account_created_date) between date('2021-07-01') and date('2021-07-31')
                )
)

, txn_data as (
    select customer_id as user_id, date(coalesce(cbs_transaction_datetime, payment_transaction_datetime)) as txn_date, 
    transaction_amount, transaction_channel, debit_card_txn_type, upi_mcc_code, reconciliation_id,
    transaction_type, bank_transfer_type, cbs_log_payer_particulars, payments_record_status,
    debit_card_msg_type
    from recon_users 
    group by 1,2,3,4,5,6,7,8,9,10,11,12
)

, off_app as 
(
    select distinct user_id,
    count(distinct case when date_trunc('month', txn_date) = date('2022-04-01') and transaction_channel is null then reconciliation_id end) as off_app_april,
    count(distinct case when date_trunc('month', txn_date) = date('2022-05-01') and transaction_channel is null then reconciliation_id end) as off_app_may,
    count(distinct case when date_trunc('month', txn_date) = date('2022-06-01') and transaction_channel is null then reconciliation_id end) as off_app_june22,
    count(distinct case when date_trunc('month', txn_date) = date('2022-07-01') and transaction_channel is null then reconciliation_id end) as off_app_july22
    from txn_data
    group by 1
)

, in_app as 
(
    select distinct user_id,
    count(distinct case when date_trunc('month', txn_date) = date('2022-04-01') and transaction_channel is not null then reconciliation_id end) as in_app_april,
    count(distinct case when date_trunc('month', txn_date) = date('2022-05-01') and transaction_channel is not null then reconciliation_id end) as in_app_may,
    count(distinct case when date_trunc('month', txn_date) = date('2022-06-01') and transaction_channel is not null then reconciliation_id end) as in_app_june22,
    count(distinct case when date_trunc('month', txn_date) = date('2022-07-01') and transaction_channel is not null then reconciliation_id end) as in_app_july22
    from txn_data
    group by 1
)


select * from (select distinct prospective_user_id from transformations_db.jupiter_onboarding_master 
where date(user_saving_account_created_date) between date('2021-07-01') and date('2021-07-31')
) a
left join off_app b on a.prospective_user_id = b.user_id
left join in_app c on a.prospective_user_id = c.user_id
order by 1


prospective_user_id  \
0     00079598-1fd1-47e9-8520-f8818b576f0f   
1     0008462f-2007-4c3f-8573-5e00cd6c59f3   
2     001753f5-7fed-47f4-b2f1-ac64279b8052   
3     001c0618-29ba-4732-8ff7-91f92143eaf1   
4     0029e614-9f2b-4c7a-bcde-7fc7a28fc887   
5     002a9aaf-b811-4f0e-b6c9-3c09396e1420   
6     002c781f-a8df-43c7-bf92-35e1566d5f37   
7     003c6026-f796-43ba-8ee1-109044cbc466   
8     005cc4b1-9087-4128-9c86-b6365525bfa4   
9     00719a9d-c3a8-49ad-93ec-02f890de3d32   
10    00901d8a-14d4-4bb1-9760-dce5eb545715   
11    00907d6c-ff7b-4878-8d07-46d3c561ba33   
12    0090d5d6-f050-4b14-86e2-4ace260b19a2   
13    009254de-8528-4ca5-babb-da7eeb2278c8   
14    00b8bcde-704e-40f2-8843-6fa8bbef5389   
15    00c2d69f-15ae-406b-84f1-5bf83b839f6f   
16    00d1a1ad-8be3-429e-9a21-451acdec1808   
17    00e22772-eb05-4a08-84af-ea5bb5598409   
18    00e4a750-639a-4855-9659-2baf04012774   
19    00f03c84-6be4-4795-abd9-d0c7bf77e288   
20    012065f8-64b8-41c4-9f5d-e084168ba59f   
21    014cae40-21cf-4320-ac08-260be2214d2d   
22    016caa2f-d73e-4154-ac28-6282f06e5724   
23    017f9607-bee8-4d0c-820c-12a6cd47e91a   
24    0185ddea-d2be-428b-9b16-45fcff568934   
25    01896f2d-4ca9-4ada-8541-508a32e76775   
26    0194ea2d-91e9-42a5-a5cb-43b9909897b4   
27    01967701-d8fc-4491-b0d3-cd782824a88a   
28    019ced76-c01b-4d1a-89db-7d053a59a1fc   
29    01b1db0b-a206-44ab-ac3b-cfb94fcd02eb   
30    01dd184c-975e-419f-937d-e4d27248e7ed   
31    021f1b13-0931-4b9c-a67e-dc3548e35b02   
32    0240de86-6109-476e-aca5-e6fc2ed30aa0   
33    0246e7b5-7e0b-4ff8-bc14-7d7c35cfaafc   
34    02887ed9-3c01-4ae8-a0eb-358ace77a572   
35    02973253-6db9-4c3a-9e70-ea90550c9015   
36    02980190-ba07-4e55-b128-517c43eb91df   
37    02a2369b-4981-4a3b-9341-9df6be63b224   
38    02c049aa-e07e-4a4b-8f70-551932fcabe7   
39    02c28885-ab93-4ec5-b243-766163cdd1a7   
40    02cf1708-8658-48be-9eaa-8ef4a98ee1f4   
41    02d0fb00-e0d3-4123-b564-a48b2923ec68   
42    02d58566-3dd2-4477-b865-60970541448f   
43    02fe0d7a-9a58-48a1-97aa-f8d3fbc8f9fa   
44                        02o-GwE-0Czg-XyS   
45    033db79b-b2b2-492a-bd6d-b71a916981eb   
46    03659c60-772b-4fe8-876f-cc12660b27e7   
47    037da6b1-d4b2-4f06-a0c4-8bdc18907ba8   
48    03844b9b-67be-45a1-8a91-06145e158c22   
49                        03K-G6o-gjig-U14   
50    03a50951-117f-4471-867b-36da6798ed30   
51    03b80241-84f8-469b-a7d8-ee802a7c81e0   
52    03d0b2f2-dd0e-45bf-b6a9-31dd9f11b7a6   
53    03d36016-ffe9-40dd-b0b3-82a80132cffa   
54    03dd7b39-2cd5-494f-ba1f-9ee95d4b57c2   
55    03ddd340-c656-4cc3-a685-a1a1c8b2278e   
56    03e20cea-d47a-4503-988f-f8ca0b427813   
57    0419bbb6-b656-41b5-8c95-9d90c9893091   
58    041abaf3-83c7-41ea-bc49-a146df569a04   
59    04370572-6f4b-4af8-978b-f76125d18459   
60    043bd45d-169e-466a-bb5f-1878ef9741b0   
61    04430727-85a0-4146-afa0-3d927ae7d2b5   
62    044ba958-1d6f-4c19-a819-0312e8941aa1   
63    045da20e-a090-4de7-bc42-3e915bd47918   
64    045fce78-a8af-4d58-b2a3-c11b89cdd9bb   
65    04629aa4-b898-4290-89e0-42b031a2c7c6   
66    046de3dc-e2a8-4fb7-b11b-326e0325276a   
67    04735c86-06ae-4414-a20e-44194e61e760   
68    047af0fc-17be-479d-a33d-abf0611bd742   
69    0486a67b-dbc5-400d-b6c2-535cf25ff6a0   
70    04961aef-f4ad-4430-880e-b5c71eae1fbd   
71    04ab2263-71a1-4b3c-bd94-3f930e6b3918   
72    04c15c32-788f-440c-8e5b-d8ab3123cda3   
73    04ce3194-73f7-476b-88f4-cd423ae595b6   
74    04d6ac7e-3c3b-4cb2-8152-d977842c6133   
75    04dd3e23-475f-40c0-a0ba-0d1e9d362bc4   
76    04f778fb-a0ee-4e1d-9e3b-f15b96817ff8   
77    04fe79fb-9677-4ba7-83c9-4eda6fa527ad   
78    0505331a-aeda-4cd8-9aee-6a38d3cf02a6   
79    05061d1c-f11a-45ba-a8bd-cf2fb24625c3   
80    050e94b9-b825-400c-b165-634aadb2ee59   
81    0528f191-84df-4bcc-a206-23dbf60a12f7   
82    0553204a-da8e-4003-8f14-54051c0dac61   
83    055e628c-1beb-42c0-81b2-7bcb0d89d12a   
84    059669dd-2165-43e8-afab-81bfe0ae4537   
85                        05D-1ZM-Em5U-mqv   
86                   